In [1]:
!pip install ultralytics wandb -U --quiet
# Enable W&B logging for Ultralytics
!yolo settings wandb=True
!wandb login d5d79f92c0bff62daeaeb2dd14bfc2f15a481769
PROJECT_NAME = 'Mosquito_Larvae_Classification-YOLO-Full-Training'

CLASSIFICATION_CHECKPOINT_FILE = "complete_runs_yolo-Full-Training.json"
CLASSIFICATION_RESULT_FILE = "yolo_classification_results-Full-Traingin.csv"
SPLITS = 5
transfer_epochs = 50
retrain_epochs = 200
transfer_patience = 10
retrain_patience = 50
#initial_learning_rate = 0.01

batch = 32

import os
import time
import wandb
import torch
import os
import pickle
import wandb
import pandas as pd
import numpy as np
import random
from typing import Dict, List, Tuple, Any
from datetime import datetime
from pathlib import Path

# Torch imports
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, Subset
from torchvision import datasets, transforms, models

from pathlib import Path
import wandb
from ultralytics import YOLO

import os
os.environ["WANDB_MODE"] = "online"
from ultralytics.cfg import get_cfg
cfg = get_cfg()
cfg.wandb = True

# Define all models
models_config = [
    {'name': 'Yolov8n-cls', 'weights': 'yolov8n-cls.pt', 'input_size': 224},
    {'name': 'Yolo11n-cls', 'weights': 'yolo11n-cls.pt', 'input_size': 224},
    {'name': 'Dilated-yolov8n-cls', 'weights': 'dilated-yolov8n-cls.pt', 'input_size': 224}
]





🔄 Cell started at: 2025-07-31 14:12:29
✅ Updated 'wandb=True'
JSONDict("/home/wanchalerm/.config/Ultralytics/settings.json"):
{
  "settings_version": "0.0.6",
  "datasets_dir": "/home/wanchalerm/pyNotebooks/datasets",
  "weights_dir": "weights",
  "runs_dir": "runs",
  "uuid": "f389f559c593bf97b54cf87b923ba1eb8c35ea8514ae818942e2dc5edf93cee4",
  "sync": true,
  "api_key": "",
  "openai_api_key": "",
  "clearml": true,
  "comet": true,
  "dvc": true,
  "hub": true,
  "mlflow": true,
  "neptune": true,
  "raytune": true,
  "tensorboard": false,
  "wandb": true,
  "vscode_msg": true,
  "openvino_msg": true
}
💡 Learn more about Ultralytics Settings at https://docs.ultralytics.com/quickstart/#ultralytics-settings
wandb: Appending key for api.wandb.ai to your netrc file: /home/wanchalerm/.netrc
wandb: W&B API key is configured. Use `wandb login --relogin` to force relogin
✅ Cell finished in 4.72 seconds



In [2]:
class WandbLogger:
    def __init__(self, project: str, entity: str = None, save_dir: str = "wandb_local"):
        self.project = project
        self.entity = entity
        self.save_dir = save_dir
        os.makedirs(self.save_dir, exist_ok=True)

        self.run = None
        self.run_name = None
        self.local_logs: List[Dict[str, Any]] = []

    def _get_timestamp(self):
        return datetime.now().strftime("%Y%m%d_%H%M%S_%f")

    def init(self, run_name: str, config: Dict[str, Any]):
        self.run_name = run_name
        try:
            self.run = wandb.init(
                project=self.project,
                entity=self.entity,
                name=run_name,
                config=config,
                resume="allow"
            )
            print(f"[WandbLogger] Online run started: {run_name}")
            self._sync_local_logs()
        except Exception as e:
            print(f"[WandbLogger] Failed to start wandb run. Logging locally. Error: {e}")
            self.run = None

    def _save_log_locally(self, log_dict: Dict[str, Any]):
        log_dict["run_name"] = self.run_name
        filename = f"{self.run_name}_{self._get_timestamp()}.pkl"
        filepath = os.path.join(self.save_dir, filename)
        with open(filepath, "wb") as f:
            pickle.dump(log_dict, f)
        print(f"[WandbLogger] Saved local log: {filepath}")

    def _sync_local_logs(self):
        files = sorted(os.listdir(self.save_dir))
        for filename in files:
            if not filename.endswith(".pkl"):
                continue
            filepath = os.path.join(self.save_dir, filename)
            try:
                with open(filepath, "rb") as f:
                    log_dict = pickle.load(f)

                if log_dict.get("run_name") != self.run_name:
                    continue

                if self.run is not None:
                    self.run.log(log_dict)
                    os.remove(filepath)
                    print(f"[WandbLogger] Synced and removed: {filepath}")
            except Exception as e:
                print(f"[WandbLogger] Failed to sync {filename}. Error: {e}")

    def log(self, log_dict: Dict[str, Any]):
        if self.run is not None:
            try:
                self.run.log(log_dict)
                self._sync_local_logs()  # Try to sync past logs
            except Exception as e:
                print(f"[WandbLogger] Logging failed. Falling back to local. Error: {e}")
                self._save_log_locally(log_dict)
        else:
            self._save_log_locally(log_dict)

    def finish(self):
        try:
            self._sync_local_logs()
            if self.run is not None:
                self.run.finish()
                print(f"[WandbLogger] Finished run: {self.run_name}")
        except Exception as e:
            print(f"[WandbLogger] Finish failed. Error: {e}")
        finally:
            self.run = None
            self.run_name = None
            



🔄 Cell started at: 2025-07-31 14:12:33
✅ Cell finished in 0.00 seconds



In [3]:
def get_input_size(architecture_name):
    for model in models_config:
        if model['name'] == architecture_name:
            return model['input_size']
    raise ValueError(f"Architecture '{architecture_name}' not found in models_config.")

def configure_device():
    """
    Detect and configure the available computing device: CUDA, MPS, or CPU.
    
    Returns:
        torch.device: Available device in priority order (CUDA > MPS > CPU)
    """
    if torch.cuda.is_available():
        device = torch.device('cuda')
        print(f"Using device: {device}")
        print(f"GPU Name: {torch.cuda.get_device_name(0)}")
        print(f"GPU Memory: {torch.cuda.get_device_properties(0).total_memory / 1e9:.2f} GB")
    elif torch.backends.mps.is_available():
        device = torch.device('mps')
        print("Using device: mps (Apple Metal Performance Shaders)")
    else:
        device = torch.device('cpu')
        print("Using device: cpu")

    return device

device = configure_device()

def set_seed(seed: int = 42):
    """
    Set random seeds for reproducibility across various libraries.
    
    Args:
        seed (int, optional): Random seed value. Defaults to 42.
    """
    # Python's built-in random module
    import random
    random.seed(seed)
    
    # Numpy
    import numpy as np
    np.random.seed(seed)
    
    # PyTorch
    import torch
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)  # For multi-GPU setups
    
    # PyTorch reproducibility settings
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False
    
    # Optional: Set environment variable for further reproducibility
    import os
    os.environ['PYTHONHASHSEED'] = str(seed)
    


🔄 Cell started at: 2025-07-31 14:12:33
Using device: cuda
GPU Name: NVIDIA GeForce RTX 4090
GPU Memory: 25.26 GB
✅ Cell finished in 0.03 seconds



In [4]:
import time
from pathlib import Path
import pandas as pd

def train_model(model, datadir, split, phase, architecture,
                freeze_backbone, epochs, patience, dataset, wandb_logger):

    # Freeze or unfreeze layers
    if freeze_backbone:
        for m in model.model.model[:-1]:  # Freeze all but last
            for p in m.parameters():
                p.requires_grad = False
        for m in model.model.model[-1:]:
            for p in m.parameters():
                p.requires_grad = True
    else:
        for p in model.model.parameters():
            p.requires_grad = True

    # Measure training time
    start_time = time.time()

    # Define run name
    run_name = datadir.replace('_Larvae', '') + '_' + str(architecture) + '_' + str(phase)

    # Train the model
    model.train(
        data=datadir,
        epochs=epochs,
        patience=patience,
        imgsz=get_input_size(architecture),
        device=device,
        verbose=False,
        project=PROJECT_NAME,
        name=run_name,
        exist_ok=True,
    )

    # Locate results.csv
    results_path = Path.cwd() / 'datasets' / run_name / 'results.csv'
    if not results_path.exists():
        raise FileNotFoundError(f"results.csv not found: {results_path}")

    # Load results
    df = pd.read_csv(results_path)

    # Runtime in seconds
    runtime = time.time() - start_time

    # Metrics from results.csv
    actual_epochs = int(df.iloc[-1]['epoch']) + 1
    best_val_loss = float(df['val/loss'].min())
    best_val_accuracy = float(df['metrics/accuracy_top1'].max())

    # Log per-epoch metrics to wandb
    for _, row in df.iterrows():
        epoch = int(row['epoch'])
        train_loss = float(row['train/loss'])
        val_loss = float(row['val/loss'])
        val_acc = float(row['metrics/accuracy_top1'])
        lr = float(row['lr/pg0'])

        wandb_logger.log({
            'epoch': epoch,
            'train_loss': train_loss,
            'val_loss': val_loss,
            'val_acc': val_acc,
            'lr': lr
        })

    # Log summary to wandb
    wandb_logger.log({
        "split": split,
        "dataset": dataset,
        "architecture": architecture,
        "Phase": phase,
        "Runtime": round(runtime, 2),  # seconds
        "epochs": epochs,
        "patience": patience,
        "actual_epochs": actual_epochs,
        "best_val_loss": round(best_val_loss, 6),
        "best_val_accuracy": round(best_val_accuracy, 4),
    })

    wandb_logger.finish()

    # Return final summary
    return {
        'actual_epochs': actual_epochs,
        'training_time': round(runtime, 2),
        'best_val_loss': round(best_val_loss, 6),
        'best_val_accuracy': round(best_val_accuracy, 4),
        'split': split,
        'dataset': dataset,
        'architecture': architecture,
        'phase': phase,
        'epochs': epochs,
        'patience': patience
    }


🔄 Cell started at: 2025-07-31 14:12:33
✅ Cell finished in 0.00 seconds



In [5]:
from pathlib import Path

def evaluate_model(
    model,                  # YOLO model object
    architecture: str,      # e.g., 'yolov8n-cls'
    dataset: str,           # 'Original' or 'Augmented'
    split: int,             # 1 through 5
    wandb_logger            # instance of WandbLogger (not None)
):
    """
    Evaluate YOLOv8 classification model on test and test-blurred datasets.
    Logs to wandb using the WandbLogger instance.

    Returns:
        dict with architecture, dataset, split, test_accuracy, blurred_test_accuracy
    """
    run_name = f"{dataset}_Split{split}_{architecture}_Evaluation"
    data_path = Path.home() / 'datasets' / f"{dataset}_Larvae_Split{split}"

    # Start wandb run
    wandb_logger.init(
        run_name=run_name,
        config={
            "architecture": architecture,
            "dataset": dataset,
            "split": split,
            "stage": "Evaluation"
        }
    )

    # --- Evaluate on test set ---
    test_yaml = data_path / 'test.yaml'
    test_results = model.val(data=str(test_yaml), split='test')
    test_accuracy = getattr(test_results, 'top1', None)

    wandb_logger.log({"test_accuracy": test_accuracy})

    # --- Evaluate on blurred test set ---
    blurred_yaml = data_path / 'test-blurred.yaml'
    blurred_results = model.val(data=str(blurred_yaml), split='test')
    blurred_accuracy = getattr(blurred_results, 'top1', None)

    wandb_logger.log({"blurred_test_accuracy": blurred_accuracy})

    # Finish wandb run
    wandb_logger.finish()

    return {
        "architecture": architecture,
        "dataset": dataset,
        "split": split,
        "test_accuracy": test_accuracy,
        "blurred_test_accuracy": blurred_accuracy
    }


🔄 Cell started at: 2025-07-31 14:12:33
✅ Cell finished in 0.00 seconds



In [6]:
import json
import os
from ultralytics import YOLO
import traceback
import pandas as pd


def main():
    # Ensure reproducibility
    set_seed()

    # Configuration
    base_dir = '../datasets'
    dataset_types = ['Original', 'Augmented']
    splits = range(1, SPLITS + 1)
    num_classes = 4

    # Initialize WandB logger (used across runs)
    wandb_logger = WandbLogger(project=PROJECT_NAME)

    # --- Load previous checkpoints ---
    if os.path.exists(CLASSIFICATION_CHECKPOINT_FILE):
        with open(CLASSIFICATION_CHECKPOINT_FILE, "r") as f:
            complete_runs = set(tuple(run) for run in json.load(f))
    else:
        complete_runs = set()

    results = []

    for model_config in models_config:
        for dataset_type in dataset_types:
            for split in splits:
                run_key = (model_config['name'], dataset_type, split)
                if run_key in complete_runs:
                    print(f"[✓] Skipping completed: {run_key}")
                    continue

                try:
                    datadir = f"{base_dir}/{dataset_type}_Larvae_Split{split}"

                    # --- Phase 1: Transfer Learning ---
                    model = YOLO(model_config['weights'])

                    phase1_result = train_model(
                        model=model,
                        datadir=datadir,
                        split=split,
                        phase="Transfer",
                        architecture=model_config['name'],
                        freeze_backbone=True,
                        epochs=transfer_epochs,
                        patience=transfer_patience,
                        dataset=dataset_type,
                        wandb_logger=wandb_logger
                    )

                    # --- Phase 2: Retrain ---
                    phase2_result = train_model(
                        model=model,
                        datadir=datadir,
                        split=split,
                        phase="Retrain",
                        architecture=model_config['name'],
                        freeze_backbone=False,
                        epochs=retrain_epochs,
                        patience=retrain_patience,
                        dataset=dataset_type,
                        wandb_logger=wandb_logger
                    )

                    # --- Evaluation ---
                    eval_result = evaluate_model(
                        model=model,
                        architecture=model_config['name'],
                        dataset=dataset_type,
                        split=split,
                        wandb_logger=wandb_logger
                    )

                    # --- Merge All Results ---
                    result_entry = {
                        'Dataset': dataset_type,
                        'Split': split,
                        'Model': model_config['name'],

                        'Transfer_Epochs': phase1_result['actual_epochs'],
                        'Transfer_Time_sec': phase1_result['training_time'],
                        'Transfer_Val_Loss': phase1_result['best_val_loss'],
                        'Transfer_Val_Acc': phase1_result['best_val_accuracy'],

                        'Retrain_Epochs': phase2_result['actual_epochs'],
                        'Retrain_Time_sec': phase2_result['training_time'],
                        'Retrain_Val_Loss': phase2_result['best_val_loss'],
                        'Retrain_Val_Acc': phase2_result['best_val_accuracy'],

                        'Test_Accuracy': eval_result['test_accuracy'],
                        'Blurred_Test_Accuracy': eval_result['blurred_test_accuracy'],
                    }

                    results.append(result_entry)

                    # ✅ Save checkpoint immediately
                    complete_runs.add(run_key)
                    with open(CLASSIFICATION_CHECKPOINT_FILE, "w") as f:
                        json.dump(list(complete_runs), f, indent=2)

                    # ✅ Append result to CSV immediately
                    df_row = pd.DataFrame([result_entry])
                    if not os.path.exists(CLASSIFICATION_RESULT_FILE):
                        df_row.to_csv(CLASSIFICATION_RESULT_FILE, index=False)
                    else:
                        df_row.to_csv(CLASSIFICATION_RESULT_FILE, mode='a', header=False, index=False)

                    print(f"[✓] Completed and logged: {run_key}")

                except Exception as e:
                    print(f"[Error] {run_key}: {e}")
                    traceback.print_exc()

    print("🏁 All training and evaluations complete.")


🔄 Cell started at: 2025-07-31 14:12:33
✅ Cell finished in 0.00 seconds



In [7]:
# Ensure reproducibility when running the script
if __name__ == '__main__':
    
    # Run main training pipeline
    main()
    
    


🔄 Cell started at: 2025-07-31 14:12:33
engine/trainer: agnostic_nms=False, amp=True, augment=False, auto_augment=randaugment, batch=16, bgr=0.0, box=7.5, cache=False, cfg=None, classes=None, close_mosaic=10, cls=0.5, conf=None, copy_paste=0.0, copy_paste_mode=flip, cos_lr=False, cutmix=0.0, data=../datasets/Original_Larvae_Split1, degrees=0.0, deterministic=True, device=None, dfl=1.5, dnn=False, dropout=0.0, dynamic=False, embed=None, epochs=50, erasing=0.4, exist_ok=True, fliplr=0.5, flipud=0.0, format=torchscript, fraction=1.0, freeze=None, half=False, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, imgsz=224, int8=False, iou=0.7, keras=False, kobj=1.0, line_width=None, lr0=0.01, lrf=0.01, mask_ratio=4, max_det=300, mixup=0.0, mode=train, model=yolov8n-cls.pt, momentum=0.937, mosaic=1.0, multi_scale=False, name=Original_Split1_Yolov8n-cls_Transfer, nbs=64, nms=False, opset=None, optimize=False, optimizer=auto, overlap_mask=True, patience=10, perspective=0.0, plots=True, pose=12.0, pretrained=Tru

wandb: Currently logged in as: wanchp (wanchp-chulalongkorn-university) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


AMP: running Automatic Mixed Precision (AMP) checks...
AMP: checks passed ✅
train: Fast image access ✅ (ping: 0.0±0.0 ms, read: 794.3±477.6 MB/s, size: 3.9 KB)


train: Scanning /home/wanchalerm/datasets/Larvae_original_split1/train... 5223 images, 0 corrupt: 100%|██████████| 5223/5223 [00:00<?, ?it/s]


val: Fast image access ✅ (ping: 0.0±0.0 ms, read: 804.2±383.0 MB/s, size: 4.0 KB)


...

test: Scanning /home/wanchalerm/datasets/NewLarvaeClassification_split5/test-normal... 4494 images, 0 corrupt: 100%|██████████| 4494/4494 [00:00<?, ?it/s]
               classes   top1_acc   top5_acc: 100%|██████████| 281/281 [00:00<00:00, 368.29it/s]


                   all      0.992          1
Speed: 0.0ms preprocess, 0.1ms inference, 0.0ms loss, 0.0ms postprocess per image
Results saved to Mosquito_Larvae_Classification-YOLO-Full-Training/Augmented_Split5_Dilated-yolov8n-cls_Retrain
Ultralytics 8.3.170 🚀 Python-3.13.2 torch-2.7.0+cu128 CUDA:0 (NVIDIA GeForce RTX 4090, 24092MiB)
test: Fast image access ✅ (ping: 0.0±0.0 ms, read: 491.5±289.4 MB/s, size: 3.1 KB)


test: Scanning /home/wanchalerm/datasets/NewLarvaeClassification_split5/test-blur... 4494 images, 0 corrupt: 100%|██████████| 4494/4494 [00:00<?, ?it/s]
               classes   top1_acc   top5_acc: 100%|██████████| 281/281 [00:00<00:00, 355.95it/s]


                   all      0.955          1
Speed: 0.0ms preprocess, 0.1ms inference, 0.0ms loss, 0.0ms postprocess per image
Results saved to Mosquito_Larvae_Classification-YOLO-Full-Training/Augmented_Split5_Dilated-yolov8n-cls_Retrain


[WandbLogger] Finished run: Augmented_Split5_Dilated-yolov8n-cls_Evaluation
[✓] Completed and logged: ('Dilated-yolov8n-cls', 'Augmented', 5)
🏁 All training and evaluations complete.
✅ Cell finished in 14h 41m 34.74s



In [8]:
def generate_summary_report(results_df):
    """
    Generate a comprehensive summary report of model performances.
    
    Args:
        results_df (pd.DataFrame): DataFrame containing training results
    """
    # Ensure matplotlib uses a backend that doesn't require a display
    import matplotlib
    matplotlib.use('Agg')
    
    import matplotlib.pyplot as plt
    import seaborn as sns
    
    # Create a directory for reports if it doesn't exist
    os.makedirs('reports', exist_ok=True)
    
    # 1. Basic Statistical Summary
    summary = results_df.groupby(['Model', 'Dataset']).agg({
        'test_accuracy': ['mean', 'std'],
        'blurred_test_accuracy': ['mean', 'std'],
        'Phase2_Training_Time': 'mean'
    }).reset_index()
    
    # Flatten multi-level column names
    summary.columns = [
        'Model', 'Dataset', 
        'Test_Accuracy_Mean', 'Test_Accuracy_Std', 
        'Blurred_Test_Accuracy_Mean', 'Blurred_Test_Accuracy_Std', 
        'Avg_Training_Time'
    ]
    
    # Save summary to CSV
    summary.to_csv('reports/model_performance_summary.csv', index=False)
    
    # 2. Detailed Visualization
    try:
        # Prepare data for plotting
        plt.figure(figsize=(15, 10))
        
        # Subplot 1: Test Accuracy Comparison
        plt.subplot(2, 2, 1)
        sns.barplot(
            x='Model', 
            y='test_accuracy', 
            hue='Dataset', 
            data=results_df,
            errorbar='sd'  # Show standard deviation
        )
        plt.title('Test Accuracy Across Models and Datasets')
        plt.xticks(rotation=45, ha='right')
        plt.tight_layout()
        
        # Subplot 2: Blurred Test Accuracy Comparison
        plt.subplot(2, 2, 2)
        sns.barplot(
            x='Model', 
            y='blurred_test_accuracy', 
            hue='Dataset', 
            data=results_df,
            errorbar='sd'
        )
        plt.title('Blurred Test Accuracy Across Models and Datasets')
        plt.xticks(rotation=45, ha='right')
        plt.tight_layout()
        
        # Subplot 3: Training Time Comparison
        plt.subplot(2, 2, 3)
        sns.boxplot(
            x='Model', 
            y='Phase2_Training_Time', 
            hue='Dataset', 
            data=results_df
        )
        plt.title('Training Time Across Models and Datasets')
        plt.xticks(rotation=45, ha='right')
        plt.tight_layout()
        
        # Subplot 4: Accuracy Difference (Test vs Blurred)
        plt.subplot(2, 2, 4)
        results_df['Accuracy_Difference'] = results_df['test_accuracy'] - results_df['blurred_test_accuracy']
        sns.boxplot(
            x='Model', 
            y='Accuracy_Difference', 
            hue='Dataset', 
            data=results_df
        )
        plt.title('Accuracy Drop (Test vs Blurred)')
        plt.xticks(rotation=45, ha='right')
        plt.tight_layout()
        
        # Save the comprehensive plot
        plt.savefig('reports/model_performance_comparison.png', dpi=300, bbox_inches='tight')
        plt.close()
    
    except Exception as e:
        print(f"Error generating visualizations: {e}")
    
    # 3. Detailed Performance Analysis
    try:
        # Performance Ranking
        performance_ranking = results_df.groupby('Model').agg({
            'test_accuracy': 'mean',
            'blurred_test_accuracy': 'mean'
        }).sort_values('test_accuracy', ascending=False)
        
        # Save ranking
        performance_ranking.to_csv('reports/model_performance_ranking.csv')
        
        # Print ranking to console
        print("\nModel Performance Ranking:")
        print(performance_ranking)
    
    except Exception as e:
        print(f"Error generating performance ranking: {e}")
    
    # 4. Detailed LaTeX Summary Table
    try:
        # Generate LaTeX table
        latex_summary = summary.to_latex(
            index=False, 
            float_format="{:.2f}".format,
            caption="Model Performance Summary"
        )
        
        with open('reports/latex_summary_table.tex', 'w') as f:
            f.write(latex_summary)
    
    except Exception as e:
        print(f"Error generating LaTeX summary: {e}")



🔄 Cell started at: 2025-08-01 04:54:08
✅ Cell finished in 0.00 seconds

